# SQLite demo notebook

### MCS 275 Spring 2021 - Emily Dumas

We'll work with the SQLite star database available from:
* [hyg_data.zip](https://dumas.io/teaching/2021/spring/mcs275/data/hyg_data.zip)
 (original source: https://github.com/astronexus/HYG-Database )

In [7]:
import os
# Set this to directory containing the database file.
# In this case, I unzipped it into the notebook dir 
# so I can just use "." (current dir)
DATADIR = "."
DBFILE = os.path.join(DATADIR,"hyg_data.sqlite")
DBFILE

'./hyg_data.sqlite'

In [8]:
os.path.exists(DBFILE)

True

In [10]:
import sqlite3
con = sqlite3.connect(DBFILE)

In [19]:
c = con.execute("SELECT proper,ra,dec,mag FROM stars LIMIT 10")
c.fetchone()

('Sol', 0.0, 0.0, -26.7)

In [20]:
c = con.execute("SELECT proper,ra,dec,mag FROM stars LIMIT 10")
c.fetchall()

[('Sol', 0.0, 0.0, -26.7),
 (None, 6e-05, 1.089009, 9.1),
 (None, 0.000283, -19.49884, 9.27),
 (None, 0.000335, 38.859279, 6.61),
 (None, 0.000569, -51.893546, 8.06),
 (None, 0.000665, -40.591202, 8.55),
 (None, 0.001246, 3.946458, 12.31),
 (None, 0.00147, 20.036114, 9.64),
 (None, 0.001823, 25.886461, 9.05),
 (None, 0.002355, 36.585958, 8.59)]

## Getting rows as dictionary-like objects

In [24]:
import sqlite3
con = sqlite3.connect(DBFILE)
con.row_factory = sqlite3.Row
# Roughly equivalent to using csv.DictReader instead of csv.reader                    

In [28]:
c = con.execute("SELECT proper,ra,dec,mag FROM stars LIMIT 10")
r = c.fetchone()

In [33]:
r["proper"]  # sqlite3.Row[columnname] gives you the value in a column

'Sol'

In [35]:
r[0]  # column 0 in the order of the query

'Sol'

In [31]:
r.keys()

['proper', 'ra', 'dec', 'mag']

In [32]:
print(r)

## Brightest stars

In [36]:
c = con.execute("SELECT proper,ra,dec,mag FROM stars ORDER BY mag LIMIT 10")
for r in c:
    print(tuple(r))

('Sol', 0.0, 0.0, -26.7)
('Sirius', 6.752481, -16.716116, -1.44)
('Canopus', 6.399195, -52.69566, -0.62)
('Arcturus', 14.26103, 19.18241, -0.05)
('Rigil Kentaurus', 14.660765, -60.833976, -0.01)
('Vega', 18.61564, 38.783692, 0.03)
('Capella', 5.27815, 45.997991, 0.08)
('Rigel', 5.242298, -8.20164, 0.18)
('Procyon', 7.655033, 5.224993, 0.4)
('Achernar', 1.628556, -57.236757, 0.45)


## All named stars

In [39]:
c = con.execute("SELECT proper,ra,dec,mag FROM stars WHERE proper IS NOT NULL;")
data = c.fetchall()
print([ r["proper"] for r in data ])


['Sol', 'Alpheratz', 'Caph', 'Algenib', 'Ankaa', 'Shedir', 'Diphda', '96 G. Psc', "Van Maanen's Star", 'Cih', 'Mirach', 'Ruchbah', 'Achernar', 'Sheratan', 'Almaak', 'Hamal', 'Mira', 'Polaris', '268 G. Cet', 'Acamar', 'Menkar', 'Algol', '82 G. Eri', 'Mirphak', 'Alcyone', 'Zaurak', 'Aldebaran', 'Hassaleh', 'Cursa', "Kapteyn's Star", 'Rigel', 'Capella', 'Bellatrix', 'Alnath', 'Nihal', 'Mintaka', 'Arneb', 'Hatsya', 'Alnilam', 'Phakt', 'Alnitak', 'Saiph', 'Betelgeuse', 'Menkalinan', 'Red Rectangle', 'Mirzam', 'Canopus', 'Alhena', 'Sirius', 'Adhara', 'Wezen', 'Aludra', 'Gomeisa', "Luyten's Star", 'Castor', 'Procyon', 'Pollux', 'Naos', 'Avior', 'Miaplacidus', 'Tureis', 'Alphard', 'Ras Elased Australis', 'Regulus', 'Algieba', 'Merak', 'Lalande 21185', 'Dubhe', 'Zosma', 'Denebola', 'Groombridge 1830', 'Phad', 'Megrez', 'Gienah Ghurab', 'Acrux', '3C 273', 'Algorab', 'Gacrux', 'Kraz', 'Porrima', 'Becrux', 'Alioth', 'Cor Caroli', 'Vindemiatrix', 'Mizar', 'Spica', 'Alcor', 'Alkaid', 'Mufrid', 'Hada

## All named stars that are also bright

In [41]:
c = con.execute("""
SELECT proper,ra,dec,mag FROM stars
WHERE proper IS NOT NULL
AND mag < 1;""")
data = c.fetchall()
print([ r["proper"] for r in data ])

['Sol', 'Achernar', 'Aldebaran', 'Rigel', 'Capella', 'Betelgeuse', 'Canopus', 'Sirius', 'Procyon', 'Acrux', 'Spica', 'Hadar', 'Arcturus', 'Rigil Kentaurus', 'Vega', 'Altair']


## Adding a table

In [44]:
import sqlite3
con = sqlite3.connect("stars2.sqlite")
con.row_factory = sqlite3.Row

In [45]:
con.execute("""CREATE TABLE named_stars_simple (
  proper TEXT,
  ra REAL,
  dec REAL,
  mag REAL,
  ci REAL
);""")

In [47]:
con.execute("""CREATE TABLE IF NOT EXISTS named_stars_simple (
  proper TEXT,
  ra REAL,
  dec REAL,
  mag REAL,
  ci REAL
);""")

In [49]:
c = con.execute("SELECT * FROM named_stars_simple;")
for r in c:
    print(tuple(r))

In [50]:
c = con.execute("""
INSERT INTO named_stars_simple (proper,ci)
VALUES ("Sun",0.6);
""")

In [51]:
c = con.execute("SELECT * FROM named_stars_simple;")
for r in c:
    print(tuple(r))

('Sun', None, None, None, 0.6)


In [52]:
c = con.execute("""
UPDATE named_stars_simple SET mag=-26 WHERE proper="Sun";
""")

In [53]:
c = con.execute("SELECT * FROM named_stars_simple;")
for r in c:
    print(tuple(r))

('Sun', None, None, -26.0, 0.6)


In [54]:
c = con.execute("""DELETE FROM named_stars_simple WHERE proper="Sun";""")

In [55]:
c = con.execute("SELECT * FROM named_stars_simple;")
for r in c:
    print(tuple(r))

In [58]:
c = con.execute("""
INSERT INTO named_stars_simple
SELECT proper,ra,dec,mag,ci FROM stars WHERE proper IS NOT NULL;
""")

In [59]:
c = con.execute("SELECT * FROM named_stars_simple;")
for r in c:
    print(tuple(r))

('Sol', 0.0, 0.0, -26.7, 0.656)
('Alpheratz', 0.139791, 29.090432, 2.07, -0.038)
('Caph', 0.152887, 59.14978, 2.28, 0.38)
('Algenib', 0.220598, 15.183596, 2.83, -0.19)
('Ankaa', 0.438056, -42.305981, 2.4, 1.083)
('Shedir', 0.675116, 56.537331, 2.24, 1.17)
('Diphda', 0.72649, -17.986605, 2.04, 1.019)
('96 G. Psc', 0.806382, 5.280615, 5.74, 0.89)
("Van Maanen's Star", 0.819416, 5.38861, 12.37, 0.554)
('Cih', 0.945143, 60.71674, 2.15, -0.046)
('Mirach', 1.162194, 35.620558, 2.07, 1.576)
('Ruchbah', 1.430216, 60.235283, 2.66, 0.16)
('Achernar', 1.628556, -57.236757, 0.45, -0.158)
('Sheratan', 1.910668, 20.808035, 2.64, 0.165)
('Almaak', 2.064984, 42.329725, 2.1, 1.37)
('Hamal', 2.119555, 23.462423, 2.01, 1.151)
('Mira', 2.322442, -2.977643, 6.47, 0.966)
('Polaris', 2.52975, 89.264109, 1.97, 0.636)
('268 G. Cet', 2.601357, 6.88687, 5.79, 0.918)
('Acamar', 2.971023, -40.304672, 2.88, 0.128)
('Menkar', 3.037992, 4.089734, 2.54, 1.63)
('Algol', 3.136148, 40.955648, 2.09, -0.003)
('82 G. Eri', 

The right way to do this would be to make a VIEW, a virtual table that always shows the results of another query (without storing anything).